#**InceptionResNetV2**

###📥 **Import Libraries**

In [ ]:
# mount drive
from google.colab import drive
drive.mount('/content/drive')

# common library
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

# tensor computation
from tensorflow.random import set_seed
from keras.preprocessing.image import ImageDataGenerator
from keras.layers import Input, Conv2D, MaxPooling2D, Flatten, Dense
from keras.utils import plot_model
from keras.models import Model, load_model
from keras.applications import InceptionResNetV2

Mounted at /content/drive


###🔒 **Inisialisasi Bilangan Random**

In [ ]:
def set_random(seed):
  np.random.seed(seed)
  set_seed(seed)

set_random(2022)

###🪆 **Data Augmentation**

In [ ]:
# file directory
file_dir = '/content/drive/Shareddrives/Teman Tapi Mining/Satria Data/2022/'
data_dir = 'data/Garbage classification/Garbage classification/'
dir = file_dir + data_dir

# train generator
train = ImageDataGenerator(
    horizontal_flip = True, vertical_flip = True,
    validation_split = 0.1, rescale = 1./255,
    shear_range = 0.1, zoom_range = 0.1,
    width_shift_range = 0.1, height_shift_range = 0.1
    )
train_generator = train.flow_from_directory(
    dir, target_size = (512, 384), batch_size = 32,
    class_mode = 'categorical', subset = 'training'
    )

# test generator
test = ImageDataGenerator(rescale = 1./255, validation_split = 0.1)
test_generator = test.flow_from_directory(
    dir, target_size = (512, 384), batch_size = 32,
    class_mode = 'categorical', subset = 'validation'
    )

Found 2276 images belonging to 6 classes.
Found 251 images belonging to 6 classes.


###🎯 **Modeling**

In [ ]:
pretrained = InceptionResNetV2(input_shape = (512, 384, 3), include_top = False, weights = 'imagenet')
pretrained.trainable = False
layers = Flatten()(pretrained.output)
layers = Dense(64, activation = 'relu')(layers)
outputs = Dense(6, activation = 'softmax')(layers)
model = Model(inputs = [pretrained.input], outputs = [outputs])

model.compile(loss = 'categorical_crossentropy', optimizer = 'adam', metrics = ['accuracy'])
model.summary()

219055592/219055592 [==============================] - 1s 0us/step
Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 512, 384, 3  0           []                               
                                )]                                                                
                                                                                                  
 conv2d (Conv2D)                (None, 255, 191, 32  864         ['input_1[0][0]']                
                                )                                                                 
                                                                                                  
 batch_normalization (BatchNorm  (None, 255, 191, 32  96         ['conv2d[0][0]']                 
 alization)                

In [ ]:
plot_model(model, show_shapes = True)

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.517034 to fit



In [ ]:
# define parameters
batch_size = 32
num_epochs = 100

# train & test steps
step_size_train = train_generator.n//train_generator.batch_size
step_size_test = test_generator.n//test_generator.batch_size

In [ ]:
history = model.fit(
    train_generator, epochs = num_epochs, steps_per_epoch = step_size_train,
    validation_data = test_generator, validation_steps = step_size_test
    )

Epoch 1/100
71/71 [==============================] - 880s 12s/step - loss: 3.6224 - accuracy: 0.6176 - val_loss: 0.8801 - val_accuracy: 0.6920
Epoch 2/100
71/71 [==============================] - 107s 1s/step - loss: 0.7888 - accuracy: 0.7384 - val_loss: 0.7025 - val_accuracy: 0.7455
Epoch 3/100
71/71 [==============================] - 107s 1s/step - loss: 0.6250 - accuracy: 0.7852 - val_loss: 0.7649 - val_accuracy: 0.7545
Epoch 4/100
71/71 [==============================] - 106s 1s/step - loss: 0.5661 - accuracy: 0.8111 - val_loss: 0.9528 - val_accuracy: 0.7455
Epoch 5/100
71/71 [==============================] - 107s 1s/step - loss: 0.5280 - accuracy: 0.8249 - val_loss: 0.7884 - val_accuracy: 0.7768
Epoch 6/100
71/71 [==============================] - 108s 2s/step - loss: 0.4768 - accuracy: 0.8400 - val_loss: 0.5874 - val_accuracy: 0.8080
Epoch 7/100
71/71 [==============================] - 107s 1s/step - loss: 0.4259 - accuracy: 0.8605 - val_loss: 0.7670 - val_accuracy: 0.8125
Epoch

In [ ]:
sns.set_style(style = 'whitegrid')

fig, axes = plt.subplots(1, 2, figsize=(20, 6))
graph = ['accuracy', 'loss']
title = ["Akurasi dan Validasi Akurasi", "Loss dan Validasi Loss"]

def draw_graph(i, text, title):
  axes[i].set_title(title)
  fig = sns.lineplot(ax = axes[i], x = history.epoch, y = history.history[text], marker = 'o')
  fig = sns.lineplot(ax = axes[i], x = history.epoch, y = history.history[f'val_{text}'], marker = 'o')
  axes[i].legend([text, f'val_{text}'])

def text_graph(i, text):
  for j, (x, y) in enumerate(zip(history.epoch, history.history[f'{text}'])):
    if j == 4:
      axes[i].text(x = x - 0.2, y = y - 0.009, s = round(y, 3), color = 'red') 
  for j, (x, y) in enumerate(zip(history.epoch, history.history[f'val_{text}'])):
    if j == 4:
      axes[i].text(x = x - 0.2, y = y - 0.009, s = round(y, 3), color = 'red') 

for i, (val, tit) in enumerate(zip(graph, title)):
    draw_graph(i, val, tit)
    text_graph(i, val)

In [ ]:
# save & load model
model.save(file_dir + 'model/InceptionResNetV2.h5')
model = load_model(file_dir + 'model/InceptionResV2.h5')

In [ ]:
# train evaluation
train_eval = model.evaluate(train_generator)
for name, value in zip(model.metrics_names, train_eval):
  print(name, ':', round(value, 5))
print()

In [ ]:
# test evaluation
test_eval = model.evaluate(test_generator)
for name, value in zip(model.metrics_names, test_eval):
  print(name, ':', round(value, 5))
print()